In [20]:
from ipyleaflet import Heatmap
import pprint
import gzip

import nagini
from nagini.core.hls.map import HLSMap

olp = nagini.resource('olp')
cat = olp.catalog_by_hrn('hrn:here:data::olp-amsterdam:nld-traffic')
layer = cat.layer_by_id('flow')
blob1 = layer.read_partitions(partition_ids=['23602974'], version=0)
blob2 = layer.read_partitions(partition_ids=['23602975'], version=0)

In [21]:
type(blob1)

generator

In [22]:
blob1 =list(blob1)
blob2 =list(blob2)
blobs_bytes1 = b''.join(blob1)
blobs_bytes2 = b''.join(blob2)
print (len((blobs_bytes1)))
print (len((blobs_bytes2)))
print(str((blobs_bytes2)))
if len(blobs_bytes2) > 57 :
    print ("both partitions ")
    decompressed= gzip.decompress(blobs_bytes1+blobs_bytes2)
else:
    print ("single partitions ")
    decompressed= gzip.decompress(blobs_bytes1)
text_file = open("Output1.txt", "w")
text_file.write(decompressed.decode("utf-8") )
text_file.close()

1308678
1308679
b'\xb4\xb3\xd8\x9c\xe4\xc9@\xca\x9a\xe0$\x174\x1d\x8e!8\xf9\xe7\x89\x8e\xf7\xe0]z\xd5\x9f\xe70l\xcf%\xdf+\x07\x93\x89W%\xda\xf7\xe9%f\x9ab\xb0vySNC\xfb\x97*k\nK\x04\\\x82e\x1e\x13b\xd0p;\xe9\xc37C\xfa\x8b\x06\x1eF\x17\x10\xd4\x91{@\xf4\x06e\xb5\xb4w\xbd\x9fA;\xf3\xc2\xee\xd4\xc7a$\x1d\xc3a\xc6\xd9\x03!\x9f\x19K\r\xcfc\x92=\x8cA\x08\xcd\x17?\x95\xb6\x9ae\x1b\x04\xcch\x18\xe17\xb4\xc3\x8b\x0b\x1c\x99\x7f\xe1\x8c\xa3\xd8\xbbp\xbb\x9c\xbf\x81\xc5\xd6BS\x1fZ\x90\xba\x8d\xd86\x84d\n\xad\x1fN\xcb\xf3\xeb?\xf3%ip6vq\xa1\x85\x0e\x1dW\xce\xa8Y\x87\'\xa1\x05\x12`\x983]9\xa3\x9b\xf2\xd6\xc1\x07\x94S\x07\x1f\x0e4\x15\xa2F\xd2U]j\xb4\x12\xe1\xc3t\xb9\\\x90k\x88\xd0~2s\x85\xf3\xce\xae\xfda\x98\xb9\x15\xd3\x0f\xf4\x15\x82\xe7\x05\x1f\x89\x95 \xfa\xf3&\x8e%\x0e\x9a1`\x9f\xcaO\xa5\x93\xaax\xa1QK\'\xf3\xb4L\xc42\x16\xad{B\x07=\xb5N\xe6\x93\xaazI\xa8\xf9\xe3\xf5d\xf8r?\xb4\x0bB\xe6\x03\x80e\n\xb4\xd89\xd5J\tf+\xaf\x94,\xbc\x98\xc4Jm\x8a\xc70\xc6\x8b\xbc\xd8\xf4\x84\xf5\x93\xc5\xcc\x18\xb14

In [23]:
import xml.etree.cElementTree as xml
ml = xml.fromstring(decompressed)
type_def = {'TR': 'THRU',
            'HV': 'HOV',
            'RA': 'RAMP'}

xlmns = '{http://traffic.here.com/trafficml-flow-3.3}'
has_offsets = False
has_slt = False
dlr_index = 0
for child in ml:
    print (child.tag, child.attrib)

{http://traffic.here.com/trafficml-flow-3.3}FEATURES {}
{http://traffic.here.com/trafficml-flow-3.3}RWS {'TY': 'TMC'}
{http://traffic.here.com/trafficml-flow-3.3}RWS {'TY': 'SHP'}
{http://traffic.here.com/trafficml-flow-3.3}diagnostic {'sfile': 'RealtimeFlowE3817-1595511596756.xml.gz|st5', 'pdd': 'trafficml-flow-dlr.33-v48'}


In [9]:
for trafficml_realtime in ml.iter(xlmns + 'TRAFFICML_REALTIME'):
            map_version = trafficml_realtime.get('MAP_VERSION')
            units = trafficml_realtime.get('UNITS')
           ## timestamp = trafficml_realtime.get('CREATED_TIMESTAMP').replace('T',' ').replace('Z','')
           ## TTAT expects timestamp in orginal format including 'T' and 'Z' 
            timestamp = trafficml_realtime.get('CREATED_TIMESTAMP')

            for rws in ml.iterfind(xlmns + 'RWS[@TY=\'SHP\']'):
                for rw in rws.iter(xlmns + 'RW'):
                    linear_id = rw.get('LI')
                    for fis in rw.iter(xlmns + 'FIS'):
                        for fi in fis.iter(xlmns + 'FI'):
                            for shp in fis.iter(xlmns + 'SHP'): 
                                print (shp.attrib)
                            for CF in fis.iter(xlmns + 'CF'): 
                                print (CF.attrib)
                                if 'JF' not in CF.attrib.keys():
                                    for sss in CF.iter(xlmns + 'SSS'):
                                        for ss in sss.iter(xlmns + 'SS'):
                                            print (ss.attrib)                                

{'FC': '4', 'LID': '54229960T', 'LE': '0.05604', 'FW': 'SD'}
{'FC': '4', 'LID': '1035491959T', 'LE': '0.06857', 'FW': 'SD'}
{'FC': '4', 'LID': '1035491958T', 'LE': '0.06966', 'FW': 'SD'}
{'FC': '4', 'LID': '1091571637T', 'LE': '0.0548', 'FW': 'SD'}
{'FC': '4', 'LID': '1091571636T', 'LE': '0.01935', 'FW': 'SD'}
{'FC': '4', 'LID': '1091571635T', 'LE': '0.01826', 'FW': 'SD'}
{'FC': '4', 'LID': '1216551921T', 'LE': '0.02508', 'FW': 'SD'}
{'FC': '4', 'LID': '1216551920T', 'LE': '0.02276', 'FW': 'SD'}
{'FC': '4', 'LID': '61491746T', 'LE': '0.01145', 'FW': 'SD'}
{'FC': '4', 'LID': '61491745T', 'LE': '0.03312', 'FW': 'SD'}
{'FC': '4', 'LID': '917739987T', 'LE': '0.02183', 'FW': 'SD'}
{'FC': '4', 'LID': '1075846189T', 'LE': '0.04102', 'FW': 'SD'}
{'FC': '4', 'LID': '1091924858T', 'LE': '0.04443', 'FW': 'SD'}
{'FC': '4', 'LID': '1091924857T', 'LE': '0.03885', 'FW': 'SD'}
{'FC': '4', 'LID': '917739985T', 'LE': '0.02058', 'FW': 'SD'}
{'FC': '4', 'LID': '1076112211T', 'LE': '0.00913', 'FW': 'SD'}
{

{'FC': '5', 'LID': '926856520F', 'LE': '0.00667', 'FW': 'SD'}
{'FC': '5', 'LID': '926856521F', 'LE': '0.06676', 'FW': 'SD'}
{'FC': '5', 'LID': '55032094F', 'LE': '0.04339', 'FW': 'SD'}
{'FC': '5', 'LID': '80090410F', 'LE': '0.01808', 'FW': 'RO'}
{'CL': '1', 'TY': 'TR', 'SP': '33.6', 'SU': '33.6', 'FF': '38.6', 'JF': '1.15065', 'CN': '0.91'}
{'FC': '4', 'LID': '888370911F', 'LE': '0.01358', 'FW': 'SD'}
{'FC': '4', 'LID': '888370912F', 'LE': '0.04479', 'FW': 'SD'}
{'FC': '4', 'LID': '54550244F', 'LE': '0.04774', 'FW': 'SD'}
{'FC': '4', 'LID': '54550245F', 'LE': '0.05044', 'FW': 'SD'}
{'FC': '4', 'LID': '888370903F', 'LE': '0.03416', 'FW': 'SD'}
{'FC': '4', 'LID': '888370904F', 'LE': '0.01224', 'FW': 'SD'}
{'FC': '4', 'LID': '759450750F', 'LE': '0.01335', 'FW': 'SD'}
{'FC': '4', 'LID': '759450751F', 'LE': '0.06335', 'FW': 'SD'}
{'FC': '4', 'LID': '759450721F', 'LE': '0.05137', 'FW': 'SD'}
{'FC': '4', 'LID': '759450722F', 'LE': '0.00995', 'FW': 'SD'}
{'FC': '4', 'LID': '759450742F', 'LE': 

{'CL': '1', 'TY': 'TR', 'SP': '14.1', 'SU': '14.1', 'FF': '18.7', 'JF': '2.18851', 'CN': '0.74'}
{'FC': '4', 'LID': '1152451833F', 'LE': '0.01992', 'FW': 'SD'}
{'FC': '4', 'LID': '1152451831F', 'LE': '0.02161', 'FW': 'SD'}
{'FC': '4', 'LID': '55035497F', 'LE': '0.09085', 'FW': 'SD'}
{'FC': '4', 'LID': '55035498F', 'LE': '0.06136', 'FW': 'SD'}
{'FC': '4', 'LID': '773726037F', 'LE': '0.03029', 'FW': 'SD'}
{'FC': '4', 'LID': '773726038F', 'LE': '0.02154', 'FW': 'SD'}
{'FC': '4', 'LID': '574886647F', 'LE': '0.19375', 'FW': 'SD'}
{'FC': '4', 'LID': '716478396F', 'LE': '0.23048', 'FW': 'SD'}
{'FC': '4', 'LID': '945554237T', 'LE': '0.07033', 'FW': 'SD'}
{'FC': '4', 'LID': '1208441843T', 'LE': '0.05902', 'FW': 'SD'}
{'FC': '4', 'LID': '1208441844F', 'LE': '0.04331', 'FW': 'SD'}
{'FC': '4', 'LID': '1152462792F', 'LE': '0.04855', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'SP': '26.21', 'SU': '26.21', 'FF': '28.6', 'JF': '0.74361', 'CN': '0.72'}
{'FC': '5', 'LID': '1076985192T', 'LE': '0.03303', 'FW': 

{'FC': '4', 'LID': '917858122F', 'LE': '0.00906', 'FW': 'SD'}
{'FC': '4', 'LID': '61515094F', 'LE': '0.01276', 'FW': 'RO'}
{'FC': '4', 'LID': '61515095F', 'LE': '0.01195', 'FW': 'RO'}
{'CL': '1', 'TY': 'TR', 'SP': '31.65', 'SU': '31.65', 'FF': '41.2', 'JF': '2.0604', 'CN': '0.9'}
{'FC': '5', 'LID': '1075728653T', 'LE': '0.05741', 'FW': 'SD'}
{'FC': '5', 'LID': '1075728652T', 'LE': '0.01825', 'FW': 'SD'}
{'FC': '5', 'LID': '54220331T', 'LE': '0.06191', 'FW': 'SD'}
{'FC': '5', 'LID': '999095604T', 'LE': '0.02122', 'FW': 'SD'}
{'FC': '5', 'LID': '999095603T', 'LE': '0.04297', 'FW': 'SD'}
{'FC': '5', 'LID': '55037736T', 'LE': '0.03942', 'FW': 'SD'}
{'FC': '5', 'LID': '55037735T', 'LE': '0.02357', 'FW': 'SD'}
{'FC': '5', 'LID': '54220509T', 'LE': '0.06629', 'FW': 'SD'}
{'FC': '5', 'LID': '574908354T', 'LE': '0.01178', 'FW': 'SD'}
{'FC': '5', 'LID': '54220546T', 'LE': '0.05338', 'FW': 'SD'}
{'FC': '5', 'LID': '54220535F', 'LE': '0.01791', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'SP': '15.09', 'S

{'FC': '5', 'LID': '1132166058F', 'LE': '0.01174', 'FW': 'SD'}
{'FC': '5', 'LID': '54218307F', 'LE': '0.02241', 'FW': 'SD'}
{'FC': '5', 'LID': '1152363277F', 'LE': '0.0477', 'FW': 'SD'}
{'FC': '5', 'LID': '1152363278F', 'LE': '0.02163', 'FW': 'SD'}
{'FC': '5', 'LID': '1152365505F', 'LE': '0.01379', 'FW': 'SD'}
{'FC': '5', 'LID': '1152365506F', 'LE': '0.01162', 'FW': 'SD'}
{'FC': '5', 'LID': '1152365507F', 'LE': '0.01667', 'FW': 'SD'}
{'FC': '5', 'LID': '1208788402F', 'LE': '0.03014', 'FW': 'SD'}
{'FC': '5', 'LID': '1208788403F', 'LE': '0.01649', 'FW': 'SD'}
{'FC': '5', 'LID': '1208788404F', 'LE': '0.01027', 'FW': 'SD'}
{'FC': '5', 'LID': '1152363582F', 'LE': '0.01449', 'FW': 'SD'}
{'FC': '5', 'LID': '1152363583F', 'LE': '0.02991', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'SP': '17.27', 'SU': '17.27', 'FF': '20.8', 'JF': '1.50977', 'CN': '0.79'}
{'FC': '5', 'LID': '999096583F', 'LE': '0.01628', 'FW': 'SD'}
{'FC': '5', 'LID': '999096584F', 'LE': '0.04062', 'FW': 'SD'}
{'FC': '5', 'LID': '5504

...

{'CL': '1', 'TY': 'TR', 'FF': '-1', 'JF': '10.0', 'TS': 'C'}
{'FC': '5', 'LID': '55060648F', 'LE': '0.02294', 'FW': 'SD'}
{'FC': '5', 'LID': '1151042232F', 'LE': '0.01953', 'FW': 'SD'}
{'FC': '5', 'LID': '54352402F', 'LE': '0.06598', 'FW': 'SD'}
{'FC': '5', 'LID': '1076960621F', 'LE': '0.04279', 'FW': 'SD'}
{'FC': '5', 'LID': '1076960622F', 'LE': '0.00593', 'FW': 'SD'}
{'FC': '5', 'LID': '999036145F', 'LE': '0.0542', 'FW': 'SD'}
{'FC': '5', 'LID': '55060652F', 'LE': '0.02063', 'FW': 'SD'}
{'FC': '5', 'LID': '591807918F', 'LE': '0.02526', 'FW': 'SD'}
{'FC': '5', 'LID': '591807919F', 'LE': '0.03145', 'FW': 'SD'}
{'FC': '5', 'LID': '591807914F', 'LE': '0.05856', 'FW': 'SD'}
{'FC': '5', 'LID': '54351731F', 'LE': '0.07096', 'FW': 'SD'}
{'FC': '5', 'LID': '1077094926F', 'LE': '0.07255', 'FW': 'SD'}
{'FC': '5', 'LID': '1077094927F', 'LE': '0.03562', 'FW': 'SD'}
{'FC': '5', 'LID': '54351370F', 'LE': '0.04977', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'FF': '20.5', 'JF': '10.0', 'TS': 'C'}
{'FC': '5

{'FC': '5', 'LID': '986454562F', 'LE': '0.16011', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'FF': '-1', 'JF': '10.0', 'TS': 'C'}
{'FC': '2', 'LID': '826603140F', 'LE': '0.0398', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'SP': '22.11', 'SU': '22.11', 'FF': '48.0', 'JF': '5.9848', 'CN': '0.97'}
{'FC': '5', 'LID': '837092719F', 'LE': '0.01731', 'FW': 'SD'}
{'FC': '5', 'LID': '1214939358F', 'LE': '0.01556', 'FW': 'SD'}
{'FC': '5', 'LID': '1214939359F', 'LE': '0.0215', 'FW': 'SD'}
{'FC': '5', 'LID': '54212921F', 'LE': '0.18577', 'FW': 'SD'}
{'FC': '5', 'LID': '913020610F', 'LE': '0.46114', 'FW': 'SD'}
{'FC': '5', 'LID': '913020612F', 'LE': '0.0603', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'SP': '46.16', 'SU': '46.16', 'FF': '47.2', 'JF': '0.19658', 'CN': '0.82'}
{'FC': '5', 'LID': '572349758T', 'LE': '0.03333', 'FW': 'SD'}
{'FC': '5', 'LID': '1076991364T', 'LE': '0.05853', 'FW': 'SD'}
{'FC': '5', 'LID': '1076991363T', 'LE': '0.01168', 'FW': 'SD'}
{'FC': '5', 'LID': '1167757496T', 'LE': '0.05372', 'FW': 'SD

{'CL': '1', 'TY': 'TR', 'SP': '18.76', 'SU': '18.76', 'FF': '23.7', 'JF': '1.85129', 'CN': '0.73'}
{'FC': '4', 'LID': '715251134F', 'LE': '0.00445', 'FW': 'SD'}
{'FC': '4', 'LID': '715251125F', 'LE': '0.05388', 'FW': 'SD'}
{'FC': '4', 'LID': '591808818F', 'LE': '0.02023', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'SP': '14.87', 'SU': '14.87', 'FF': '37.9', 'JF': '3.14159', 'CN': '0.9'}
{'FC': '5', 'LID': '54353140F', 'LE': '0.00986', 'FW': 'SD'}
{'FC': '5', 'LID': '54353129F', 'LE': '0.10832', 'FW': 'SD'}
{'FC': '5', 'LID': '54352983F', 'LE': '0.05188', 'FW': 'SD'}
{'FC': '5', 'LID': '54352892F', 'LE': '0.01083', 'FW': 'SD'}
{'FC': '5', 'LID': '54352866F', 'LE': '0.12232', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'SP': '14.16', 'SU': '14.16', 'FF': '20.2', 'JF': '2.65978', 'CN': '0.77'}
{'FC': '5', 'LID': '574907576F', 'LE': '0.00681', 'FW': 'SD'}
{'FC': '5', 'LID': '1091272945F', 'LE': '0.0643', 'FW': 'SD'}
{'FC': '5', 'LID': '1091272946F', 'LE': '0.04083', 'FW': 'SD'}
{'FC': '5', 'LID': '109127

{'FC': '5', 'LID': '1152325268T', 'LE': '0.00953', 'FW': 'SD'}
{'FC': '5', 'LID': '1152325267T', 'LE': '0.05519', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'SP': '17.13', 'SU': '17.13', 'FF': '15.8', 'JF': '0.0', 'CN': '0.87'}
{'FC': '2', 'LID': '837884471T', 'LE': '0.02013', 'FW': 'RA'}
{'CL': '1', 'TY': 'RA', 'SP': '19.91', 'SU': '19.91', 'FF': '70.0', 'JF': '7.67871', 'CN': '0.75'}
{'FC': '5', 'LID': '985818422T', 'LE': '0.02254', 'FW': 'SD'}
{'FC': '5', 'LID': '1075716436T', 'LE': '0.01759', 'FW': 'SD'}
{'FC': '5', 'LID': '1075716435T', 'LE': '0.06124', 'FW': 'SD'}
{'FC': '5', 'LID': '1152167182T', 'LE': '0.02019', 'FW': 'SD'}
{'FC': '5', 'LID': '1152167181T', 'LE': '0.0795', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'SP': '10.37', 'SU': '10.37', 'FF': '17.3', 'JF': '3.56173', 'CN': '0.73'}
{'FC': '5', 'LID': '61474607F', 'LE': '0.36941', 'FW': 'SD'}
{'FC': '5', 'LID': '61474608F', 'LE': '0.22651', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'SP': '6.07', 'SU': '6.07', 'FF': '20.0', 'JF': '8.39365', '

{'FC': '5', 'LID': '999064347T', 'LE': '0.01773', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'SP': '11.14', 'SU': '11.14', 'FF': '12.7', 'JF': '1.09272', 'CN': '0.79'}
{'FC': '3', 'LID': '54233894T', 'LE': '0.02778', 'FW': 'SD'}
{'CL': '1', 'TY': 'TR', 'SP': '27.41', 'SU': '27.41', 'FF': '33.0', 'JF': '1.50673', 'CN': '0.99'}
{'FC': '5', 'LID': '1121717753F', 'LE': '0.01636', 'FW': 'SD'}
{'FC': '5', 'LID': '1121717754F', 'LE': '0.01728', 'FW': 'SD'}
{'FC': '5', 'LID': '1233890322F', 'LE': '0.05436', 'FW': 'SD'}
{'FC': '5', 'LID': '1204628450F', 'LE': '0.04592', 'FW': 'SD'}
{'FC': '5', 'LID': '1204628460F', 'LE': '0.03624', 'FW': 'SD'}
{'FC': '5', 'LID': '1204628456F', 'LE': '0.01641', 'FW': 'SD'}
{'FC': '5', 'LID': '1204628457F', 'LE': '0.01957', 'FW': 'SD'}
{'FC': '5', 'LID': '1232648386F', 'LE': '0.01867', 'FW': 'SD'}
{'FC': '5', 'LID': '1232648387F', 'LE': '0.03808', 'FW': 'SD'}
{'FC': '5', 'LID': '1233893338T', 'LE': '0.07821', 'FW': 'SD'}
{'FC': '5', 'LID': '1235992984T', 'LE': '0.08764'